In [1]:
import sys
sys.path.append('../')

import pandas as pd
import numpy as np
import math
from timeit import default_timer as timer
from datetime import datetime, timedelta
import numba
from ensemble_processing import load_data, load, save
import keras

/Users/neilkloot/anaconda/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [ ]:
pd.options.display.max_rows=500
pd.options.display.max_columns=500

In [46]:
def return_week_summary(df, median_cols, sum_cols, mode_cols):
    # assumes a datetime index
    resample_methods = {}
    # First create object with all fields defined
    for col in median_cols:
        resample_methods[col] = 'median'

    for col in sum_cols:
        resample_methods[col] = 'sum'

    for col in mode_cols:
        resample_methods[col] = 'mode'

    return df[median_cols].resample('1W').apply(resample_methods)


# test_df = pd.DataFrame({
#     'dates': ['2018-01-02', '2018-01-03', '2018-01-04', '2018-03-05', '2019-04-09'],
#     'val': [1, 2, 2, 3, 3],
#     'date2': ['2019-01-02', '2019-01-03','2019-02-02', '2019-02-03', '2019-05-05']
# })
# test_df['dates'] = pd.to_datetime(test_df['dates'], errors='coerce')
# test_df['date2'] = pd.to_datetime(test_df['date2'], errors='coerce')
# test_df.sort_values(by=['dates'], inplace=True)
# print(test_df.dtypes)
# test_df.set_index('dates', inplace=True)
# print(test_df)
# print(test_df.index)
# print(test_df.index.week, test_df.index.year)
# return_week_median(test_df)

In [ ]:
import sklearn
sklearn.__version__

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
data_prefix = 'ml-20190416'
# Load data

print('Loading data...')
all_df = pd.read_pickle('../data/' + data_prefix + '-data.pkl.gz', compression='gzip')


Loading data...


In [6]:
print(all_df.columns)

Index(['symbol', 'quoteDate', 'lastTradePriceOnly', 'adjustedPrice', 'volume',
       'daysHigh', 'daysLow', 'previousClose', 'change', 'changeInPercent',
       ...
       'Future12WeekReturn', 'Future12WeekRiskAdjustedReturn',
       'Future26WeekDividend', 'Future26WeekPrice', 'Future26WeekReturn',
       'Future26WeekRiskAdjustedReturn', 'Future52WeekDividend',
       'Future52WeekPrice', 'Future52WeekReturn',
       'Future52WeekRiskAdjustedReturn'],
      dtype='object', length=132)


In [23]:
symbol_industry_path = '../data/symbol-industry-lookup.csv'
# extract and save symbol list
symbols = all_df['symbol'].dropna().drop_duplicates().to_frame()
symbols.to_csv('../data/ml-' + data_prefix + '-symbols-list.csv')


# check whether each symbol has a match in the industry categories set
categories_df = pd.read_csv(symbol_industry_path)
categories_df = symbols.merge(categories_df, left_on='symbol', right_on='symbol', how='left')
print('Checking for any null columns')
has_nulls = categories_df.isnull().any().any()
if has_nulls:
    print('WARNING - Found nulls vals')
    print(categories_df[categories_df.isnull().any(axis=1)])
    raise('Symbols missing matching category records')
else:
    print('No nulls found')

Checking for any null columns
No nulls found


In [30]:
import glob

def return_existing_symbol_list(path, run_str):
    existing_symbol_list = []

    print('Checking for files from', path)
    # Return files in path
    file_list = glob.glob(path + 'ml-symbol-*' + run_str + '.pkl.gz')

    # load each model set
    for file_name in file_list:
        # remove leading path and trailing file extension
        symbol = file_name.replace(
            path, '').replace('ml-symbol-', '').replace('-' + run_str + '.pkl.gz', '')

        # create model property and load model set into it
        existing_symbol_list.append(symbol)

    return existing_symbol_list

In [33]:
return_existing_symbol_list('../data/', '20190416')

Checking for files from ../data/


[]

In [36]:
from optimise_dataframe import optimise_df

def retrieve_symbol_dfs(path, run_str):
    """
        Retrieves the infividual dataframes saved during pre-processing and returns them 
    """
    symbol_dfs = []

    print('Checking for files from', path)
    # Return files in path
    file_list = glob.glob(path + 'ml-symbol-*' + run_str + '.pkl.gz')

    # load each model set
    for file_name in file_list:
        # retrieve data frame and append to list
        symbol_df = pd.read_pickle(file_name, compression='gzip')
        symbol_df = optimise_df(symbol_df)

        symbol_dfs.append(symbol_df)

    print('Concatenating symbol dfs')
    # Create empty data frame
    output_df = pd.concat(symbol_dfs)

    print('Optimising symbol dfs')
    output_df = optimise_df(output_df)

    return output_df

In [53]:
concat_df = retrieve_symbol_dfs('../data/', '20190416')
concat_df

Checking for files from ../data/
Concatenating symbol dfs


/Users/neilkloot/anaconda/lib/python3.6/site-packages/ipykernel_launcher.py:23: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



Optimising symbol dfs


52WeekHigh  52WeekLow  640106_A3597525W  AINTCOV  \
quoteDate_ref                                                     
2018-05-14          0.750      0.390        112.599998   -15.35   
2018-05-15          0.750      0.390        112.599998      NaN   
2018-05-16          0.750      0.390               NaN      NaN   
2018-05-17          0.750      0.390        112.599998      NaN   
2018-05-18          0.750      0.390        112.599998      NaN   
2018-05-21          0.750      0.390        112.599998      NaN   
2018-05-22          0.750      0.390        112.599998      NaN   
2018-05-23          0.750      0.390        112.599998      NaN   
2018-05-24          0.750      0.390        112.599998      NaN   
2018-05-25          0.750      0.390        112.599998      NaN   
2018-05-27          0.750      0.390               NaN      NaN   
2018-05-28          0.750      0.390        112.599998      NaN   
2018-05-29          0.750      0.390               NaN      NaN   
2018-05-30          0.750      0.390        112.599998      NaN   
2018-05-31          0.750      0.390        112.599998      NaN   
2018-06-01          0.750      0.390        112.599998      NaN   
2018-06-03          0.750      0.390               NaN      NaN   
2018-06-04          0.750      0.390        112.599998      NaN   
2018-06-05          0.750      0.390        112.599998      NaN   
2018-06-06          0.750      0.390        112.599998      NaN   
2018-06-07          0.750      0.390        112.599998      NaN   
2018-06-08          0.750      0.390        112.599998      NaN   
2018-06-12          0.750      0.390        112.599998      NaN   
2018-06-13          0.750      0.390        112.599998      NaN   
2018-06-14          0.750      0.390        112.599998      NaN   
2018-06-15          0.750      0.390        112.599998      NaN   
2018-06-18          0.750      0.390        112.599998      NaN   
2018-06-19          0.750      0.390        112.599998      NaN   
2018-06-20          0.750      0.390        112.599998      NaN   
2018-06-21          0.750      0.390        112.599998      NaN   
...                   ...        ...               ...      ...   
2014-10-09          0.029      0.005               NaN      NaN   
2014-10-10          0.029      0.005               NaN      NaN   
2014-10-13          0.029      0.005               NaN      NaN   
2014-10-14          0.029      0.005        105.900002      NaN   
2014-10-15          0.029      0.005               NaN      NaN   
2014-10-16          0.029      0.005        105.900002      NaN   
2014-10-17          0.029      0.005               NaN      NaN   
2014-10-20          0.029      0.005        105.900002      NaN   
2014-10-21          0.029      0.005        105.900002      NaN   
2014-10-22          0.029      0.005        105.900002      NaN   
2014-10-23          0.029      0.005        105.900002      NaN   
2014-10-24          0.029      0.005               NaN      NaN   
2014-10-27          0.029      0.005               NaN      NaN   
2014-10-28          0.029      0.005               NaN      NaN   
2014-10-29          0.029      0.005               NaN      NaN   
2014-10-30          0.029      0.005               NaN      NaN   
2014-10-31          0.029      0.005               NaN      NaN   
2014-11-03          0.029      0.005               NaN      NaN   
2014-11-04          0.029      0.005        106.400002      NaN   
2014-11-05          0.029      0.005               NaN      NaN   
2014-11-06          0.029      0.005               NaN      NaN   
2014-11-07          0.029      0.005               NaN      NaN   
2014-11-10          0.029      0.005        106.400002      NaN   
2014-11-11          0.029      0.005               NaN      NaN   
2014-11-12          0.029      0.005        106.400002      NaN   
2014-11-13          0.029      0.004        106.400002      NaN   
2014-11-14          0.029      0.004        106.400002      Na

In [43]:
concat_df[concat_df.index > '2019-01-30']

52WeekHigh  52WeekLow  640106_A3597525W  AINTCOV  \
quoteDate_ref                                                     
2019-01-31        0.67546      0.265               NaN      NaN   
2019-02-01        0.67546      0.265        113.500000      NaN   
2019-02-03        0.67546      0.265               NaN      NaN   
2019-02-04        0.66581      0.265        113.500000      NaN   
2019-02-05        0.66581      0.265               NaN      NaN   
2019-02-06        0.62722      0.265        114.099998      NaN   
2019-02-07        0.62722      0.265        114.099998      NaN   
2019-02-08        0.62722      0.265               NaN      NaN   
2019-02-10        0.62722      0.265               NaN      NaN   
2019-02-11        0.61757      0.265        114.099998      NaN   
2019-02-12        0.61757      0.265        114.099998      NaN   
2019-02-13        0.61757      0.265               NaN      NaN   
2019-02-14        0.61757      0.265               NaN      NaN   
2019-02-15        0.61757      0.265        114.099998      NaN   
2019-02-17        0.61757      0.265               NaN      NaN   
2019-02-18        0.61757      0.265        114.099998      NaN   
2019-02-19        0.61757      0.265               NaN      NaN   
2019-02-20        0.61757      0.265        114.099998      NaN   
2019-02-21        0.61757      0.265        114.099998      NaN   
2019-02-22        0.61757      0.265        114.099998      NaN   
2019-02-24        0.61757      0.265               NaN      NaN   
2019-02-25        0.61757      0.265        114.099998      NaN   
2019-02-26        0.61757      0.265        114.099998      NaN   
2019-02-27        0.61757      0.265        114.099998      NaN   
2019-02-28        0.61757      0.265               NaN      NaN   
2019-03-01        0.61757      0.265        114.099998      NaN   
2019-03-03        0.61757      0.265               NaN      NaN   
2019-03-04        0.61757      0.265        114.099998      NaN   
2019-03-05        0.61757      0.265        114.099998      NaN   
2019-03-06        0.61757      0.265        114.099998      NaN   
...                   ...        ...               ...      ...   
2019-03-11        1.08000      0.047        114.099998      NaN   
2019-03-12        1.08000      0.047        114.099998      NaN   
2019-03-13        1.08000      0.047        114.099998      NaN   
2019-03-14        1.08000      0.047        114.099998      NaN   
2019-03-15        1.08000      0.047        114.099998      NaN   
2019-03-17        1.08000      0.047               NaN      NaN   
2019-03-18        1.08000      0.047        114.099998      NaN   
2019-03-19        1.08000      0.047        114.099998      NaN   
2019-03-20        1.08000      0.047        114.099998      NaN   
2019-03-21        1.08000      0.047        114.099998      NaN   
2019-03-22        1.08000      0.042        114.099998      NaN   
2019-03-24        1.08000      0.042               NaN      NaN   
2019-03-25        1.08000      0.042        114.099998      NaN   
2019-03-26        1.08000      0.042        114.099998      NaN   
2019-03-27        1.08000      0.039        114.099998      NaN   
2019-03-28        1.08000      0.039        114.099998      NaN   
2019-03-29        1.08000      0.039        114.099998      NaN   
2019-03-31        1.08000      0.039               NaN      NaN   
2019-04-01        1.08000      0.039        114.099998      NaN   
2019-04-02        1.08000      0.039        114.099998      NaN   
2019-04-03        1.08000      0.039        114.099998      NaN   
2019-04-04        1.08000      0.039               NaN      NaN   
2019-04-05        1.08000      0.039        114.099998      NaN   
2019-04-07        1.08000      0.039               NaN      NaN   
2019-04-08        1.08000      0.039        114.099998      NaN   
2019-04-09        1.08000      0.039        114.099998      NaN   
2019-04-10        1.08000      0.037        114.099998      Na

In [69]:
from processing_constants import ALL_CONTINUOUS_COLUMNS, HIGH_NAN_COLUMNS
from processing_constants import BOLLINGER_PREDICTION_COLUMNS, BOLLINGER_VALUE_COLUMNS
ID_COLUMNS = ['symbol', 'GICSSector', 'GICSIndustryGroup', 'GICSIndustry']
DATE_COLS = ['exDividendDate']



concat_df[ALL_CONTINUOUS_COLUMNS]
concat_df[BOLLINGER_PREDICTION_COLUMNS]
concat_df[BOLLINGER_VALUE_COLUMNS]
concat_df[ID_COLUMNS]



all_defined_cols = []
all_defined_cols.extend(ALL_CONTINUOUS_COLUMNS)
all_defined_cols.extend(BOLLINGER_PREDICTION_COLUMNS)
all_defined_cols.extend(BOLLINGER_VALUE_COLUMNS)
all_defined_cols.extend(ID_COLUMNS)
all_defined_cols.extend(DATE_COLS)

median_cols = []
median_cols.extend(ALL_CONTINUOUS_COLUMNS)
median_cols.extend(DATE_COLS)

sum_cols = ['sumVolume']

mode_cols = []
mode_cols.extend(BOLLINGER_PREDICTION_COLUMNS)
mode_cols.extend(BOLLINGER_VALUE_COLUMNS)
mode_cols.extend(ID_COLUMNS)

concat_cols = concat_df.columns.values

print('All cols: ', str(len(all_defined_cols)))
print('df cols:', str(len(concat_cols)))

print('df vals not in list')
for col in concat_cols:
    if col not in all_defined_cols: print(col)
        
print('list vals not in df')
for col in all_defined_cols:
#     print(col)
    if col not in concat_cols: print(col)



All cols:  394
df cols: 222
df vals not in list
sumVolume
list vals not in df


In [97]:
from scipy import stats
from processing_constants import ALL_CONTINUOUS_COLUMNS, HIGH_NAN_COLUMNS
from processing_constants import BOLLINGER_PREDICTION_COLUMNS, BOLLINGER_VALUE_COLUMNS
ID_COLUMNS = ['symbol', 'GICSSector', 'GICSIndustryGroup', 'GICSIndustry']
DATE_COLS = ['exDividendDate']

def return_week_summary(df, median_cols, sum_cols, mode_cols):
    # assumes a datetime index
    if len(median_cols):
        median_resample = temp_symbol_df[median_cols].resample('1W').median()
    else:
        median_resample = pd.DataFrame()

    if len(sum_cols):
        sum_resample = temp_symbol_df[sum_cols].resample('1W').sum()
    else:
        sum_resample = pd.DataFrame()

    if len(mode_cols):
        mode_resample = temp_symbol_df[mode_cols].resample('1W').apply(lambda x: stats.mode(x)[0][0])
    else:
        mode_resample = pd.DataFrame()    

    return pd.concat([median_resample, sum_resample, mode_resample], axis=1)


temp_symbol_df = pd.read_pickle('../data/ml-symbol-CDH-20190416.pkl.gz', compression='gzip')

temp_symbol_df.drop(HIGH_NAN_COLUMNS, axis=1, inplace=True, errors='ignore')
temp_symbol_df.drop(['quoteDate'], axis=1, inplace=True, errors='ignore')
temp_symbol_df['sumVolume'] = temp_symbol_df['volume']

all_defined_cols = []
all_defined_cols.extend(ALL_CONTINUOUS_COLUMNS)
all_defined_cols.extend(BOLLINGER_PREDICTION_COLUMNS)
all_defined_cols.extend(BOLLINGER_VALUE_COLUMNS)
all_defined_cols.extend(ID_COLUMNS)
all_defined_cols.extend(DATE_COLS)

median_cols = []
median_cols.extend(ALL_CONTINUOUS_COLUMNS)
median_cols.extend(DATE_COLS)

sum_cols = ['sumVolume']

mode_cols = []
mode_cols.extend(BOLLINGER_PREDICTION_COLUMNS)
mode_cols.extend(BOLLINGER_VALUE_COLUMNS)
mode_cols.extend(ID_COLUMNS)

summary_df = return_week_summary(temp_symbol_df, median_cols, sum_cols, mode_cols)
summary_df

/Users/neilkloot/anaconda/lib/python3.6/site-packages/scipy/stats/stats.py:253: RuntimeWarning: The input array could not be properly checked for nan values. nan values will be ignored.
  "values. nan values will be ignored.", RuntimeWarning)


lastTradePriceOnly  adjustedPrice  quoteDate_TIMESTAMP  volume  \
quoteDate_ref                                                                   
2007-07-22                 0.0360         0.0360           16934400.0       0   
2007-07-29                    NaN         0.0360                  NaN       0   
2007-08-05                    NaN         0.0360                  NaN       0   
2007-08-12                 0.0380         0.0360           19094400.0       0   
2007-08-19                 0.0370         0.0380           19612800.0       0   
2007-08-26                    NaN         0.0370                  NaN       0   
2007-09-02                    NaN         0.0370                  NaN       0   
2007-09-09                 0.0440         0.0440           21340800.0       0   
2007-09-16                    NaN         0.0440                  NaN       0   
2007-09-23                    NaN         0.0440                  NaN       0   
2007-09-30                    NaN         0.0440                  NaN       0   
2007-10-07                    NaN         0.0440                  NaN       0   
2007-10-14                    NaN         0.0440                  NaN       0   
2007-10-21                    NaN         0.0440                  NaN       0   
2007-10-28                    NaN         0.0440                  NaN       0   
2007-11-04                    NaN         0.0440                  NaN       0   
2007-11-11                    NaN         0.0440                  NaN       0   
2007-11-18                    NaN         0.0440                  NaN       0   
2007-11-25                    NaN         0.0440                  NaN       0   
2007-12-02                    NaN         0.0440                  NaN       0   
2007-12-09                    NaN         0.0440                  NaN       0   
2007-12-16                    NaN         0.0440                  NaN       0   
2007-12-23                    NaN         0.0440                  NaN       0   
2007-12-30                 0.0290         0.0440           31190400.0       0   
2008-01-06                 0.0300         0.0295           31708800.0       0   
2008-01-13                 0.0300         0.0300           32227200.0       0   
2008-01-20                 0.0350         0.0350           32832000.0       0   
2008-01-27                    NaN         0.0350                  NaN       0   
2008-02-03                    NaN         0.0350                  NaN       0   
2008-02-10                    NaN         0.0350                  NaN       0   
2008-02-17                    NaN         0.0350                  NaN       0   
2008-02-24                    NaN         0.0350                  NaN       0   
2008-03-02                    NaN         0.0350                  NaN       0   
2008-03-09                    NaN         0.0350                  NaN       0   
2008-03-16                    NaN         0.0350                  NaN       0   
2008-03-23                    NaN         0.0350                  NaN       0   
2008-03-30                    NaN         0.0350                  NaN       0   
2008-04-06                    NaN         0.0350                  NaN       0   
2008-04-13                    NaN         0.0350                  NaN       0   
2008-04-20                    NaN         0.0350                  NaN       0   
2008-04-27                    NaN         0.0350                  NaN       0   
2008-05-04                 0.0225         0.0230           41904000.0       0   
2008-05-11                 0.0230         0.0230           42595200.0       0   
2008-05-18                 0.0230         0.0230           42940800.0       0   
2008-05-25                 0.0240         0.0240           43632000.0       0   
2008-06-01                    NaN         0.0240                  NaN       0   
2008-06-08                    NaN         0.0240                  NaN       0   
2008-06-15                 0.0230         0.02

In [86]:
temp_symbol_df[mode_cols].resample('1W').apply(lambda x: stats.mode(x)[0][0])

/Users/neilkloot/anaconda/lib/python3.6/site-packages/scipy/stats/stats.py:253: RuntimeWarning: The input array could not be properly checked for nan values. nan values will be ignored.
  "values. nan values will be ignored.", RuntimeWarning)


one_week_bollinger_prediction two_week_bollinger_prediction  \
quoteDate_ref                                                               
2007-07-22                           Steady                        Steady   
2007-07-29                           Steady                        Steady   
2007-08-05                           Steady                        Steady   
2007-08-12                           Steady                        Steady   
2007-08-19                           Steady                        Steady   
2007-08-26                           Steady                        Steady   
2007-09-02                           Steady                        Steady   
2007-09-09                           Steady                        Steady   
2007-09-16                           Steady                        Steady   
2007-09-23                           Steady                        Steady   
2007-09-30                           Steady                        Steady   
2007-10-07                           Steady                        Steady   
2007-10-14                           Steady                        Steady   
2007-10-21                           Steady                        Steady   
2007-10-28                           Steady                        Steady   
2007-11-04                           Steady                        Steady   
2007-11-11                           Steady                        Steady   
2007-11-18                           Steady                        Steady   
2007-11-25                           Steady                        Steady   
2007-12-02                           Steady                        Steady   
2007-12-09                           Steady                        Steady   
2007-12-16                           Steady                        Steady   
2007-12-23                           Steady                        Steady   
2007-12-30                           Steady                        Steady   
2008-01-06                           Steady                        Steady   
2008-01-13                           Steady                        Steady   
2008-01-20                           Steady                        Steady   
2008-01-27                           Steady                        Steady   
2008-02-03                           Steady                        Steady   
2008-02-10                           Steady                        Steady   
...                                     ...                           ...   
2018-07-15                           Steady                        Steady   
2018-07-22                           Steady                        Steady   
2018-07-29                           Steady                        Steady   
2018-08-05                           Steady                        Steady   
2018-08-12                           Steady                        Steady   
2018-08-19                           Steady                        Steady   
2018-08-26                           Steady                        Steady   
2018-09-02                           Steady                        Steady   
2018-09-09                           Steady                        Steady   
2018-09-16                           Steady                        Steady   
2018-09-23                           Steady                        Steady   
2018-09-30                           Steady                        Steady   
2018-10-07                           Steady                        Steady   
2018-10-14                           Steady                        Steady   
2018-10-21                           Steady                        Steady   
2018-10-28                           Steady                        Steady   
2018-11-04                           Steady                        Steady   
2018-11-11                           Steady                        Steady   
2018-11-18                           Steady                        Steady   
2018-11-25

In [96]:
pd.options.display.max_rows=500
pd.options.display.max_columns=500